In [2]:
import pandas as pd

df = pd.read_csv('meta.csv')

df

source_file  n_rows  n_cols  \
0    ./train_separated/data_DEEPSEEKforTextClassifi...   17595     678   
1    ./train_separated/data_DEEPSEEKforTextClassifi...   19203     678   
2    ./train_separated/data_DEEPSEEKforTextClassifi...   18854     678   
3    ./train_separated/data_DEEPSEEKforTextClassifi...   17782     678   
4    ./train_separated/data_DEEPSEEKforTextClassifi...   17700     678   
..                                                 ...     ...     ...   
675  ./infer_separated/infer_ViTL16forImageSemantic...      93     678   
676  ./infer_separated/infer_ViTL16forImageSemantic...      94     678   
677  ./infer_separated/infer_ViTL16forImageSemantic...     106     678   
678  ./infer_separated/infer_ViTL16forImageSemantic...     114     678   
679  ./infer_separated/infer_ViTL16forImageSemantic...     105     678   

           phase    mode     model                       task  dataset  \
0    fine-tuning     llm  DEEPSEEK         TextClassification  default   
1    fine-tuning     llm  DEEPSEEK         TextClassification  default   
2    fine-tuning     llm  DEEPSEEK         TextClassification  default   
3    fine-tuning     llm  DEEPSEEK         TextClassification  default   
4    fine-tuning     llm  DEEPSEEK         TextClassification  default   
..           ...     ...       ...                        ...      ...   
675        infer  nonllm    ViTL16  ImageSemanticSegmentation  default   
676        infer  nonllm    ViTL16  ImageSemanticSegmentation  default   
677        infer  nonllm    ViTL16  ImageSemanticSegmentation  default   
678        infer  nonllm    ViTL16  ImageSemanticSegmentation  default   
679        infer  nonllm    ViTL16  ImageSemanticSegmentation  default   

                            model_task  \
0         DEEPSEEK__TextClassification   
1         DEEPSEEK__TextClassification   
2         DEEPSEEK__TextClassification   
3         DEEPSEEK__TextClassification   
4         DEEPSEEK__TextClassification   
..                                 ...   
675  ViTL16__ImageSemanticSegmentation   
676  ViTL16__ImageSemanticSegmentation   
677  ViTL16__ImageSemanticSegmentation   
678  ViTL16__ImageSemanticSegmentation   
679  ViTL16__ImageSemanticSegmentation   

                                       workload  
0         DEEPSEEK__TextClassification__default  
1         DEEPSEEK__TextClassification__default  
2         DEEPSEEK__TextClassification__default  
3         DEEPSEEK__TextClassification__default  
4         DEEPSEEK__TextClassification__default  
..                                          ...  
675  ViTL16__ImageSemanticSegmentation__default  
676  ViTL16__ImageSemanticSegmentation__default  
677  ViTL16__ImageSemanticSegmentation__default  
678  ViTL16__ImageSemanticSegmentation__default  
679  ViTL16__ImageSemanticSegmentation__default  

[680 rows x 10 columns]

In [3]:
import re
import pandas as pd

# ==== Network-related Metrics Description Text ====
network_text = """
NetworkInterStat_diff:rx_bytes.*.*[Bytes] — Bytes received on <Interface> during sample window (delta).
NetworkInterStat_diff:rx_packets.*.*[count] — Packets received during window (delta).
NetworkInterStat_diff:rx_errs.*.*[count] — Receive errors in window (delta).
NetworkInterStat_diff:rx_drop.*.*[count] — Received packets dropped in window (delta).
NetworkInterStat_diff:rx_fifo.*.*[count] — RX FIFO errors in window (delta).
NetworkInterStat_diff:rx_frame.*.*[count] — RX frame alignment errors in window (delta).
NetworkInterStat_diff:rx_compressed.*.*[count] — Compressed Rx packets in window (delta).
NetworkInterStat_diff:rx_multicast.*.*[count] — Multicast Rx packets in window (delta).
NetworkInterStat_diff:tx_bytes.*.*[Bytes] — Bytes transmitted on <Interface> during window (delta).
NetworkInterStat_diff:tx_packets.*.*[count] — Packets transmitted during window (delta).
NetworkInterStat_diff:tx_errs.*.*[count] — Transmit errors in window (delta).
NetworkInterStat_diff:tx_drop.*.*[count] — Transmit drops in window (delta).
NetworkInterStat_diff:tx_fifo.*.*[count] — TX FIFO errors in window (delta).
NetworkInterStat_diff:tx_colls.*.*[count] — TX collisions in window (delta).
NetworkInterStat_diff:tx_carrier.*.*[count] — Carrier errors on TX in window (delta).
NetworkInterStat_diff:tx_compressed.*.*[count] — Compressed Tx packets in window (delta).
NetworkInterStat_diff:NetworkUtilization.*.*[%] — Interface bandwidth utilization percent for the sample window (sampled / derived).
NetworkProtocolCounts:TCP.*[count] — Number of TCP connections (instant or sampled depending on collector).
NetworkProtocolCounts:UDP.*[count] — Number of UDP endpoints/sockets (instant).
NetworkProtocolCounts:UNIX.*[count] — Number of UNIX domain sockets (instant).
NetworkProtocolCounts:RAW.*[count] — Raw sockets count (instant).
NetworkProtocolCounts:DCCP.*[count] — DCCP sockets count (instant, if applicable).
NetworkProtocolCounts:SCTP.*[count] — SCTP connections count (instant, if applicable).
NetworkProtocolCounts:local_to.*[count] — Local-to connection count (collector-defined semantics).
NetworkProtocolCounts:to_local.*[count] — To-local connection count (collector-defined semantics).
NetworkProtocolCounts:total_connections.*[count] — Total tracked connections (instant / sampled).
NetworkTCPRetrans_diff:TcpRetransSegs.*[count] — TCP retransmitted segments in the sample window (delta).
NetworkTCPRetrans_diff:TcpExtTCPSynRetrans.*[count] — TCP SYN retransmissions in window (delta).
NetworkTCPRetrans_diff:TcpExtTCPLostRetransmit.*[count] — Retransmissions that were subsequently lost (delta).
"""

# ==== Extract Metrics and Descriptions ====
network_metrics = re.findall(r"^([A-Za-z0-9_:.*\[\]]+)\s+—\s+(.*)$", network_text, flags=re.M)
df_metrics = pd.DataFrame(network_metrics, columns=["metric_pattern", "description"])


In [4]:
# ==== Only focus on 'llm' mode and 'infer' phase ====
for file in df[(df['mode'] == 'llm') & (df['phase'] == 'infer')]['source_file'].tolist():
    print(f"Reading: {file}")
    data = pd.read_csv(file, sep='\t', header=0)

    # ==== Find matching columns based on the memory patterns ====
    matched_cols = []
    for pattern in df_metrics["metric_pattern"]:
        # Replace .* in the regular expression with the actual regular expression matching pattern
        regex = pattern.replace(".*", ".*")
        matched = [col for col in data.columns if re.match(regex, col)]
        matched_cols.extend(matched)

    # Deduplication and sorting
    matched_cols = list(sorted(set(matched_cols)))

    print(f"Matched {len(matched_cols)} columns:")
    print(matched_cols)

    # ==== Extract data from these columns ====
    data_selected = data[matched_cols]

    # ==== Optional: Merge description information (matching by regular expression pattern) ====
    # Create a mapping for metric_name -> description (using the first matching rule)
    desc_map = {}
    for _, row in df_metrics.iterrows():
        regex = row['metric_pattern'].replace(".*", ".*")
        for col in matched_cols:
            if re.match(regex, col):
                desc_map[col] = row['description']

    desc_df = pd.DataFrame(list(desc_map.items()), columns=["metric_name", "description"])

    # display(desc_df.head())
    display(data_selected.head())

    # break

Reading: ./infer_separated/data_DEEPSEEKforInference_default_2025-04-26T09-41-59_htc-g003.txt
Matched 44 columns:
['NetworkInterStat_diff:rx_bytes.ens1f0.htc-g003[Bytes]', 'NetworkInterStat_diff:rx_bytes.ib0.htc-g003[Bytes]', 'NetworkInterStat_diff:rx_compressed.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_compressed.ib0.htc-g003[count]', 'NetworkInterStat_diff:rx_drop.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_drop.ib0.htc-g003[count]', 'NetworkInterStat_diff:rx_errs.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_errs.ib0.htc-g003[count]', 'NetworkInterStat_diff:rx_fifo.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_fifo.ib0.htc-g003[count]', 'NetworkInterStat_diff:rx_frame.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_frame.ib0.htc-g003[count]', 'NetworkInterStat_diff:rx_multicast.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_multicast.ib0.htc-g003[count]', 'NetworkInterStat_diff:rx_packets.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_packets.ib0

NetworkInterStat_diff:rx_bytes.ens1f0.htc-g003[Bytes]  \
0                                         21504048.0       
1                                         31028162.0       
2                                         40552276.0       
3                                         50076390.0       
4                                         59600504.0       

   NetworkInterStat_diff:rx_bytes.ib0.htc-g003[Bytes]  \
0                                             5662.0    
1                                             4602.5    
2                                             3543.0    
3                                             2483.5    
4                                             1424.0    

   NetworkInterStat_diff:rx_compressed.ens1f0.htc-g003[count]  \
0                                                0.0            
1                                                0.0            
2                                                0.0            
3                                                0.0            
4                                                0.0            

   NetworkInterStat_diff:rx_compressed.ib0.htc-g003[count]  \
0                                                0.0         
1                                                0.0         
2                                                0.0         
3                                                0.0         
4                                                0.0         

   NetworkInterStat_diff:rx_drop.ens1f0.htc-g003[count]  \
0                                               1.00      
1                                               0.75      
2                                               0.50      
3                                               0.25      
4                                               0.00      

   NetworkInterStat_diff:rx_drop.ib0.htc-g003[count]  \
0                                                0.0   
1                                                0.0   
2                                                0.0   
3                                                0.0   
4                                                0.0   

   NetworkInterStat_diff:rx_errs.ens1f0.htc-g003[count]  \
0                                                0.0      
1                                                0.0      
2                                                0.0      
3                                                0.0      
4                                                0.0      

   NetworkInterStat_diff:rx_errs.ib0.htc-g003[count]  \
0                                                0.0   
1                                                0.0   
2                                                0.0   
3                                                0.0   
4                                                0.0   

   NetworkInterStat_diff:rx_fifo.ens1f0.htc-g003[count]  \
0                                                0.0      
1                                                0.0      
2                                                0.0      
3                                                0.0      
4                                                0.0      

   NetworkInterStat_diff:rx_fifo.ib0.htc-g003[count]  ...  \
0                                                0.0  ...   
1                                                0.0  ...   
2                                                0.0  ...   
3                                                0.0  ...   
4                                                0.0  ...   

   NetworkProtocolCounts:SCTP.htc-g003[count]  \
0                                         0.0   
1                                         0.0   
2                                         0.0   
3                                         0.0   
4                                         0.0   

   NetworkProtocolCounts:TCP.htc-g003[count]  \
0                                       65.2   
1                                     

Reading: ./infer_separated/data_DEEPSEEKforInference_default_2025-04-26T17-25-16_htc-g003.txt
Matched 44 columns:
['NetworkInterStat_diff:rx_bytes.ens1f0.htc-g003[Bytes]', 'NetworkInterStat_diff:rx_bytes.ib0.htc-g003[Bytes]', 'NetworkInterStat_diff:rx_compressed.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_compressed.ib0.htc-g003[count]', 'NetworkInterStat_diff:rx_drop.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_drop.ib0.htc-g003[count]', 'NetworkInterStat_diff:rx_errs.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_errs.ib0.htc-g003[count]', 'NetworkInterStat_diff:rx_fifo.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_fifo.ib0.htc-g003[count]', 'NetworkInterStat_diff:rx_frame.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_frame.ib0.htc-g003[count]', 'NetworkInterStat_diff:rx_multicast.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_multicast.ib0.htc-g003[count]', 'NetworkInterStat_diff:rx_packets.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_packets.ib0

NetworkInterStat_diff:rx_bytes.ens1f0.htc-g003[Bytes]  \
0                                                NaN       
1                                                NaN       
2                                                NaN       
3                                         12506853.0       
4                                         18448372.0       

   NetworkInterStat_diff:rx_bytes.ib0.htc-g003[Bytes]  \
0                                                NaN    
1                                                NaN    
2                                                NaN    
3                                       11156.000000    
4                                        7862.666667    

   NetworkInterStat_diff:rx_compressed.ens1f0.htc-g003[count]  \
0                                                NaN            
1                                                NaN            
2                                                NaN            
3                                                0.0            
4                                                0.0            

   NetworkInterStat_diff:rx_compressed.ib0.htc-g003[count]  \
0                                                NaN         
1                                                NaN         
2                                                NaN         
3                                                0.0         
4                                                0.0         

   NetworkInterStat_diff:rx_drop.ens1f0.htc-g003[count]  \
0                                                NaN      
1                                                NaN      
2                                                NaN      
3                                                0.0      
4                                                0.0      

   NetworkInterStat_diff:rx_drop.ib0.htc-g003[count]  \
0                                                NaN   
1                                                NaN   
2                                                NaN   
3                                                0.0   
4                                                0.0   

   NetworkInterStat_diff:rx_errs.ens1f0.htc-g003[count]  \
0                                                NaN      
1                                                NaN      
2                                                NaN      
3                                                0.0      
4                                                0.0      

   NetworkInterStat_diff:rx_errs.ib0.htc-g003[count]  \
0                                                NaN   
1                                                NaN   
2                                                NaN   
3                                                0.0   
4                                                0.0   

   NetworkInterStat_diff:rx_fifo.ens1f0.htc-g003[count]  \
0                                                NaN      
1                                                NaN      
2                                                NaN      
3                                                0.0      
4                                                0.0      

   NetworkInterStat_diff:rx_fifo.ib0.htc-g003[count]  ...  \
0                                                NaN  ...   
1                                                NaN  ...   
2                                                NaN  ...   
3                                                0.0  ...   
4                                                0.0  ...   

   NetworkProtocolCounts:SCTP.htc-g003[count]  \
0                                         NaN   
1                                         0.0   
2                                         0.0   
3                                         0.0   
4                                         0.0   

   NetworkProtocolCounts:TCP.htc-g003[count]  \
0                                        NaN   
1                                     

Reading: ./infer_separated/data_DEEPSEEKforInference_default_2025-04-27T01-02-52_htc-g003.txt
Matched 44 columns:
['NetworkInterStat_diff:rx_bytes.ens1f0.htc-g003[Bytes]', 'NetworkInterStat_diff:rx_bytes.ib0.htc-g003[Bytes]', 'NetworkInterStat_diff:rx_compressed.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_compressed.ib0.htc-g003[count]', 'NetworkInterStat_diff:rx_drop.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_drop.ib0.htc-g003[count]', 'NetworkInterStat_diff:rx_errs.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_errs.ib0.htc-g003[count]', 'NetworkInterStat_diff:rx_fifo.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_fifo.ib0.htc-g003[count]', 'NetworkInterStat_diff:rx_frame.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_frame.ib0.htc-g003[count]', 'NetworkInterStat_diff:rx_multicast.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_multicast.ib0.htc-g003[count]', 'NetworkInterStat_diff:rx_packets.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_packets.ib0

...

NetworkInterStat_diff:rx_bytes.ens1f0.htc-g003[Bytes]  \
0                                       1.342895e+07       
1                                       2.419965e+07       
2                                       3.497034e+07       
3                                       4.574104e+07       
4                                       5.651174e+07       

   NetworkInterStat_diff:rx_bytes.ib0.htc-g003[Bytes]  \
0                                        6287.142857    
1                                        7696.285714    
2                                        9105.428571    
3                                       10514.571429    
4                                       11923.714286    

   NetworkInterStat_diff:rx_compressed.ens1f0.htc-g003[count]  \
0                                                0.0            
1                                                0.0            
2                                                0.0            
3                                                0.0            
4                                                0.0            

   NetworkInterStat_diff:rx_compressed.ib0.htc-g003[count]  \
0                                                0.0         
1                                                0.0         
2                                                0.0         
3                                                0.0         
4                                                0.0         

   NetworkInterStat_diff:rx_drop.ens1f0.htc-g003[count]  \
0                                                0.0      
1                                                0.0      
2                                                0.0      
3                                                0.0      
4                                                0.0      

   NetworkInterStat_diff:rx_drop.ib0.htc-g003[count]  \
0                                                0.0   
1                                                0.0   
2                                                0.0   
3                                                0.0   
4                                                0.0   

   NetworkInterStat_diff:rx_errs.ens1f0.htc-g003[count]  \
0                                                0.0      
1                                                0.0      
2                                                0.0      
3                                                0.0      
4                                                0.0      

   NetworkInterStat_diff:rx_errs.ib0.htc-g003[count]  \
0                                                0.0   
1                                                0.0   
2                                                0.0   
3                                                0.0   
4                                                0.0   

   NetworkInterStat_diff:rx_fifo.ens1f0.htc-g003[count]  \
0                                                0.0      
1                                                0.0      
2                                                0.0      
3                                                0.0      
4                                                0.0      

   NetworkInterStat_diff:rx_fifo.ib0.htc-g003[count]  ...  \
0                                                0.0  ...   
1                                                0.0  ...   
2                                                0.0  ...   
3                                                0.0  ...   
4                                                0.0  ...   

   NetworkProtocolCounts:SCTP.htc-g003[count]  \
0                                         0.0   
1                                         0.0   
2                                         0.0   
3                                         0.0   
4                                         0.0   

   NetworkProtocolCounts:TCP.htc-g003[count]  \
0                                  73.000000   
1                                  72.

Reading: ./infer_separated/data_MISTRALforInference_default_2025-04-28T20-43-02_htc-g003.txt
Matched 44 columns:
['NetworkInterStat_diff:rx_bytes.ens1f0.htc-g003[Bytes]', 'NetworkInterStat_diff:rx_bytes.ib0.htc-g003[Bytes]', 'NetworkInterStat_diff:rx_compressed.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_compressed.ib0.htc-g003[count]', 'NetworkInterStat_diff:rx_drop.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_drop.ib0.htc-g003[count]', 'NetworkInterStat_diff:rx_errs.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_errs.ib0.htc-g003[count]', 'NetworkInterStat_diff:rx_fifo.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_fifo.ib0.htc-g003[count]', 'NetworkInterStat_diff:rx_frame.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_frame.ib0.htc-g003[count]', 'NetworkInterStat_diff:rx_multicast.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_multicast.ib0.htc-g003[count]', 'NetworkInterStat_diff:rx_packets.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_packets.ib0.

NetworkInterStat_diff:rx_bytes.ens1f0.htc-g003[Bytes]  \
0                                        21511728.00       
1                                        29985832.25       
2                                        38459936.50       
3                                        46934040.75       
4                                        55408145.00       

   NetworkInterStat_diff:rx_bytes.ib0.htc-g003[Bytes]  \
0                                             2352.0    
1                                             4549.0    
2                                             6746.0    
3                                             8943.0    
4                                            11140.0    

   NetworkInterStat_diff:rx_compressed.ens1f0.htc-g003[count]  \
0                                                0.0            
1                                                0.0            
2                                                0.0            
3                                                0.0            
4                                                0.0            

   NetworkInterStat_diff:rx_compressed.ib0.htc-g003[count]  \
0                                                0.0         
1                                                0.0         
2                                                0.0         
3                                                0.0         
4                                                0.0         

   NetworkInterStat_diff:rx_drop.ens1f0.htc-g003[count]  \
0                                               0.00      
1                                               0.25      
2                                               0.50      
3                                               0.75      
4                                               1.00      

   NetworkInterStat_diff:rx_drop.ib0.htc-g003[count]  \
0                                                0.0   
1                                                0.0   
2                                                0.0   
3                                                0.0   
4                                                0.0   

   NetworkInterStat_diff:rx_errs.ens1f0.htc-g003[count]  \
0                                                0.0      
1                                                0.0      
2                                                0.0      
3                                                0.0      
4                                                0.0      

   NetworkInterStat_diff:rx_errs.ib0.htc-g003[count]  \
0                                                0.0   
1                                                0.0   
2                                                0.0   
3                                                0.0   
4                                                0.0   

   NetworkInterStat_diff:rx_fifo.ens1f0.htc-g003[count]  \
0                                                0.0      
1                                                0.0      
2                                                0.0      
3                                                0.0      
4                                                0.0      

   NetworkInterStat_diff:rx_fifo.ib0.htc-g003[count]  ...  \
0                                                0.0  ...   
1                                                0.0  ...   
2                                                0.0  ...   
3                                                0.0  ...   
4                                                0.0  ...   

   NetworkProtocolCounts:SCTP.htc-g003[count]  \
0                                         0.0   
1                                         0.0   
2                                         0.0   
3                                         0.0   
4                                         0.0   

   NetworkProtocolCounts:TCP.htc-g003[count]  \
0                                      68.00   
1                                     

Reading: ./infer_separated/data_MISTRALforInference_default_2025-04-29T04-11-47_htc-g003.txt
Matched 44 columns:
['NetworkInterStat_diff:rx_bytes.ens1f0.htc-g003[Bytes]', 'NetworkInterStat_diff:rx_bytes.ib0.htc-g003[Bytes]', 'NetworkInterStat_diff:rx_compressed.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_compressed.ib0.htc-g003[count]', 'NetworkInterStat_diff:rx_drop.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_drop.ib0.htc-g003[count]', 'NetworkInterStat_diff:rx_errs.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_errs.ib0.htc-g003[count]', 'NetworkInterStat_diff:rx_fifo.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_fifo.ib0.htc-g003[count]', 'NetworkInterStat_diff:rx_frame.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_frame.ib0.htc-g003[count]', 'NetworkInterStat_diff:rx_multicast.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_multicast.ib0.htc-g003[count]', 'NetworkInterStat_diff:rx_packets.ens1f0.htc-g003[count]', 'NetworkInterStat_diff:rx_packets.ib0.

NetworkInterStat_diff:rx_bytes.ens1f0.htc-g003[Bytes]  \
0                                         13535942.0       
1                                         23096714.0       
2                                         32657486.0       
3                                         42218258.0       
4                                         51779030.0       

   NetworkInterStat_diff:rx_bytes.ib0.htc-g003[Bytes]  \
0                                             2352.0    
1                                             4739.2    
2                                             7126.4    
3                                             9513.6    
4                                            11900.8    

   NetworkInterStat_diff:rx_compressed.ens1f0.htc-g003[count]  \
0                                                0.0            
1                                                0.0            
2                                                0.0            
3                                                0.0            
4                                                0.0            

   NetworkInterStat_diff:rx_compressed.ib0.htc-g003[count]  \
0                                                0.0         
1                                                0.0         
2                                                0.0         
3                                                0.0         
4                                                0.0         

   NetworkInterStat_diff:rx_drop.ens1f0.htc-g003[count]  \
0                                                0.0      
1                                                0.0      
2                                                0.0      
3                                                0.0      
4                                                0.0      

   NetworkInterStat_diff:rx_drop.ib0.htc-g003[count]  \
0                                                0.0   
1                                                0.0   
2                                                0.0   
3                                                0.0   
4                                                0.0   

   NetworkInterStat_diff:rx_errs.ens1f0.htc-g003[count]  \
0                                                0.0      
1                                                0.0      
2                                                0.0      
3                                                0.0      
4                                                0.0      

   NetworkInterStat_diff:rx_errs.ib0.htc-g003[count]  \
0                                                0.0   
1                                                0.0   
2                                                0.0   
3                                                0.0   
4                                                0.0   

   NetworkInterStat_diff:rx_fifo.ens1f0.htc-g003[count]  \
0                                                0.0      
1                                                0.0      
2                                                0.0      
3                                                0.0      
4                                                0.0      

   NetworkInterStat_diff:rx_fifo.ib0.htc-g003[count]  ...  \
0                                                0.0  ...   
1                                                0.0  ...   
2                                                0.0  ...   
3                                                0.0  ...   
4                                                0.0  ...   

   NetworkProtocolCounts:SCTP.htc-g003[count]  \
0                                         0.0   
1                                         0.0   
2                                         0.0   
3                                         0.0   
4                                         0.0   

   NetworkProtocolCounts:TCP.htc-g003[count]  \
0                                       71.0   
1                                     